In [0]:
import numpy
from tensorflow.contrib.tensorboard.plugins import projector
import os

**Mounting drive to hosted runtime**




In [2]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


**Loading the training and test embeddings as wells as the corresponding class labels from the hosted runtime**

In [0]:
train_emb=numpy.load('/content/gdrive/My Drive/train_embeddings.npy')
test_emb=numpy.load('/content/gdrive/My Drive/test_embeddings.npy')
train_labels=numpy.load('/content/gdrive/My Drive/train_labels.npy',allow_pickle=True)
test_labels=numpy.load('/content/gdrive/My Drive/test_labels.npy',allow_pickle=True)

**Making training metadata class file from the train_labels**

In [0]:
log_dir='Logs/'
if not os.path.exists(log_dir):
  os.mkdir(log_dir)
train_label_tmp=[]
numpy.savetxt(log_dir+'train_feature_vectors_samples.txt',train_emb)
numpy.savetxt(log_dir+'test_feature_vectors_samples.txt',test_emb)
metadata_train_file = open(os.path.join(log_dir, 'metadata_train_classes.tsv'), 'w')
metadata_train_file.write('Class\tName\n')
j=0
count=0
for i in train_labels:
  c=i[0]
  if(count==0):
    train_label_tmp.append(i[0])
    count=count+1
  else:
    if(train_label_tmp[-1]==i[0]):
      count=count+1
    else:
      train_label_tmp.append(i[0])
      count=count+1
      j=j+1
  metadata_train_file.write('{}\t{}\n'.format(j,c))
metadata_train_file.close()
  

**Making testing metadata class file from the test_labels**

In [0]:
test_label_tmp=[]
metadata_test_file = open(os.path.join(log_dir, 'metadata_test_classes.tsv'), 'w')
metadata_test_file.write('Class\tName\n')
j=0
count=0
for i in test_labels:
  c=i[0]
  if(count==0):
    test_label_tmp.append(i[0])
    count=count+1
  else:
    if(test_label_tmp[-1]==i[0]):
      count=count+1
    else:
      test_label_tmp.append(i[0])
      count=count+1
      j=j+1
  metadata_test_file.write('{}\t{}\n'.format(j,c))
metadata_test_file.close()

**Creating Train and Test tensors for training and testing features**

In [0]:
import tensorflow as tf
train_feature_vector=numpy.loadtxt(log_dir+'train_feature_vectors_samples.txt')
test_feature_vector=numpy.loadtxt(log_dir+'test_feature_vectors_samples.txt')
train_features = tf.Variable(train_feature_vector, name='train_features')
test_features = tf.Variable(test_feature_vector, name='test_features')

**Configuring the Tensorboard projector with the train tensor initialized prior**

In [0]:
with tf.Session() as sess:
  saver=tf.train.Saver([train_features])
  sess.run(train_features.initializer)
  saver.save(sess,os.path.join(log_dir,'train.ckpt'))
  config=projector.ProjectorConfig()
  embedding=config.embeddings.add()
  embedding.tensor_name=train_features.name
  #embedding.metadata_path=os.path.join(log_dir, 'metadata_train_classes.tsv')
  projector.visualize_embeddings(tf.summary.FileWriter(log_dir),config)

**Loading in-built notebook extension for tensorboard**

In [8]:
!pip install tensorboardcolab
%load_ext tensorboard

**Running tensorboard inline on the files created in the Log Directory of tensorflow session**

In [9]:
%tensorboard --logdir /content/Logs

Output hidden; open in https://colab.research.google.com to view.